In [1]:
# Copyright 2024 Keysight Technologies Inc.

In [2]:
import keysight.qcs as qcs

# set the following to True when connected to hardware:
run_on_hw = False

# instantiate channels representing two AWGs and two digitizers
# Index `0` of these virtual channels are mapped to channels on chassis 1
# Index `1` of these virtual channels are mapped to channels on chassis 2
awgs = qcs.Channels(range(2), "readoutawg")
digs = qcs.Channels(range(2), "readoutreceiver")

mapper = qcs.load("../../assets/channel_map.qcs")

In [3]:
# create a program for the first chassis
program1 = qcs.Program()
gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), 1, 4.15e9)
program1.add_waveform(gauss, awgs[0])
program1.add_acquisition(80e-9, digs[0])
program1.n_shots(10)

Program([Layer(Channels(labels=[0], name=readoutawg, absolute_phase=False)=[RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=_implicit, value=1.0, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4150000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad))], Channels(labels=[0], name=readoutreceiver, absolute_phase=False)=[Acquisition(Scalar(name=_implicit, value=8e-08, dtype=float, unit=s))])])

In [4]:
# create a program for the second chassis
program2 = qcs.Program()
gauss = qcs.RFWaveform(80e-9, qcs.GaussianEnvelope(num_sigma=4), 1, 4.15e9)
program2.add_waveform(gauss, awgs[1])
program2.add_acquisition(80e-9, digs[1])
program2.n_shots(10)

Program([Layer(Channels(labels=[1], name=readoutawg, absolute_phase=False)=[RFWaveform(duration=Scalar(name=_implicit, value=8e-08, dtype=float, unit=s), envelope={GaussianEnvelope(4.0): Scalar(name=_implicit, value=1.0, dtype=float, unit=none)}, rf_frequency=Scalar(name=_implicit, value=4150000000.0, dtype=float, unit=Hz), instantaneous_phase={GaussianEnvelope(4.0): Scalar(name=_implicit, value=0.0, dtype=float, unit=rad)}, post_phase=Scalar(name=_implicit, value=0.0, dtype=float, unit=rad))], Channels(labels=[1], name=readoutreceiver, absolute_phase=False)=[Acquisition(Scalar(name=_implicit, value=8e-08, dtype=float, unit=s))])])

In [5]:
if run_on_hw:
    # initialize the backend pass
    backend = qcs.HclBackend(channel_mapper=mapper, blocking=False)
    # Submit the first program for execution
    program1 = qcs.Executor(backend).execute(program1)
    # Submit the secon program for execution before while the first program is running.
    program2 = qcs.Executor(backend).execute(program2)

In [6]:
if run_on_hw:

    prog1_state = backend.get_program_state(program1.results.accession_id)
    prog1_completed = backend.is_program_completed(program1.results.accession_id)
    print(f"Program Chassis 1 state: {prog1_state}. Completed: {prog1_completed}")

    prog2_state = backend.get_program_state(program2.results.accession_id)
    prog2_completed = backend.is_program_completed(program2.results.accession_id)
    print(f"Program Chassis 2 state: {prog2_state}. Completed: {prog2_completed}")

In [7]:
if run_on_hw:
    if prog1_completed:
        trace_data1 = program1.get_trace()
    if prog2_completed:
        trace_data2 = program2.get_trace()